In [ ]:
!pip install google-colab-selenium[undetected]
!pip install html5lib
import google_colab_selenium as gs
from selenium.webdriver.common.by import By
from selenium import webdriver
import time
#Option allows us to give selenium additional parameters
from selenium.webdriver.chrome.options import Options
from bs4 import BeautifulSoup
#io will make a string appear to be read from disk
from io import StringIO
import pandas as pd
import requests
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import json

In [ ]:
url = 'https://www.datacenters.com/locations/canada'
response = requests.get(url)
response.text

'\n<!DOCTYPE html>\n<html>\n  <head>\n    <meta name="viewport" content="width=device-width, initial-scale=1.0">\n    <title>Canada Data Centers - Providers Map in Canada</title>\n    <meta name="description" content="Data Centers in Canada with map. List of available providers and facilities in Canada, including Colocation, Bare Metal Servers, and IaaS Data Centers.">\n    <!-- See https://www.abuseipdb.com/ -->\n    <meta name="abuseipdb-verification" content="DRUAmm7d" />\n\n        <!-- OneTrust Cookies Consent Notice start for datacenters.com -->\n  <script src="https://cdn.cookielaw.org/scripttemplates/otSDKStub.js"  type="text/javascript" charset="UTF-8" data-domain-script="c27244d4-b08b-4f0a-8fea-93f49234c91a" ></script>\n  <script type="text/javascript">\n    function OptanonWrapper() { }\n  </script>\n  <!-- OneTrust Cookies Consent Notice end for datacenters.com -->\n\n\n    <script>\n  window.RAILS_ENV = \'production\';\n  window.GA_TID = \'UA-46812924-1\';\n    window.SENT

In [ ]:
driver = gs.Chrome()
driver.get(url)


<IPython.core.display.Javascript object>

In [ ]:
driver.page_source

'<html><head>\n    <meta name="viewport" content="width=device-width, initial-scale=1.0">\n    <title>Canada Data Centers - Providers Map in Canada</title>\n    <meta name="description" content="Data Centers in Canada with map. List of available providers and facilities in Canada, including Colocation, Bare Metal Servers, and IaaS Data Centers.">\n    <!-- See https://www.abuseipdb.com/ -->\n    <meta name="abuseipdb-verification" content="DRUAmm7d">\n\n        <!-- OneTrust Cookies Consent Notice start for datacenters.com -->\n  <script async="" src="https://www.googletagmanager.com/gtm.js?id=GTM-KL6NZ94&amp;gtm_auth=2BbtG33W87IQEfI0Hj-ZYw&amp;gtm_preview=env-2&amp;gtm_cookies_win=x"></script><script async="" src="https://www.google-analytics.com/analytics.js"></script><script async="" src="https://www.google-analytics.com/analytics.js"></script><script async="" src="https://www.google-analytics.com/analytics.js"></script><script async="" src="https://www.google-analytics.com/analytic

In [ ]:
href_collection = []
c_name_collection = []
c_address_collection = []
while True:
    # Extract inner HTML of the data center container
    dataCenter = driver.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div[2]/div[3]').get_attribute('innerHTML')
    dataCenter_soup = BeautifulSoup(dataCenter, 'html.parser')

    # Find all links with the specified class
    link_list = dataCenter_soup.find_all('a', {'class': 'flex flex-col gap-2 rounded border border-gray-100 p-2 hover:border-teal-300 hover:shadow-lg hover:shadow-teal-600/40'})
    name_list = dataCenter_soup.find_all('div', {'class': 'text font-medium hover:text-purple'})
    address_list = dataCenter_soup.find_all('div', {'class': 'text-xs text-gray-500'})
    for a in link_list:
        if 'href' in a.attrs:
            href_collection.append(a["href"])
    for name in name_list:
      c_name_collection.append(name.text)
    for div in address_list:
      prev_sibling = div.find_previous_sibling('div', {'class': 'text font-medium hover:text-purple'})
      if prev_sibling:
        address = div.text.strip()
        c_address_collection.append(address)

    # Try to find and click the next button
    try:
      next_button = driver.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div[2]/div[3]/div[2]/div[1]/nav/button[5]')
      next_button.click()
      time.sleep(3)
    except Exception as e:
        # next_button = driver.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div[2]/div[3]/div[2]/div[1]/nav/button[9]')
        print(f'No more pages to navigate.{e}')
        break
driver.quit()
href_dict = pd.DataFrame(href_collection)
c_name_dict = pd.DataFrame(c_name_collection)
c_address_dict = pd.DataFrame(c_address_collection)

No more pages to navigate.Message: element click intercepted: Element <button class="Control__control__ijHLR Pagination__pageItem__NsQSw Pagination__disabled__FbUC6 Pagination__symbol__KHv6r" type="button">...</button> is not clickable at point (227, 421). Other element would receive the click: <nav>...</nav>
  (Session info: chrome=135.0.7049.95)
Stacktrace:
#0 0x59cd96c50cea <unknown>
#1 0x59cd967015f0 <unknown>
#2 0x59cd9675987c <unknown>
#3 0x59cd967576dc <unknown>
#4 0x59cd96754d72 <unknown>
#5 0x59cd96754467 <unknown>
#6 0x59cd96746b3d <unknown>
#7 0x59cd96778662 <unknown>
#8 0x59cd967464ba <unknown>
#9 0x59cd9677882e <unknown>
#10 0x59cd9679e660 <unknown>
#11 0x59cd96778433 <unknown>
#12 0x59cd96744ea3 <unknown>
#13 0x59cd96745b01 <unknown>
#14 0x59cd96c15b3b <unknown>
#15 0x59cd96c19a21 <unknown>
#16 0x59cd96bfcc32 <unknown>
#17 0x59cd96c1a594 <unknown>
#18 0x59cd96be0eef <unknown>
#19 0x59cd96c3ed98 <unknown>
#20 0x59cd96c3ef76 <unknown>
#21 0x59cd96c4fb36 <unknown>
#22 0x7b1b

In [ ]:
c_name_dict

0
0                 Canada Central-Toronto
1               TR2 Toronto Data Centers
2           MT1 Montreal IBX Data Center
3            CL3 Calgary IBX Data Center
4    YYZ1 Mississauga Data Center Campus
..                                   ...
186                Quebec Data Center II
187                  Ontario Data Center
188                  Alberta Data Center
189                     DC01 Data Center
190              DC1 Toronto Data Center

[191 rows x 1 columns]

In [ ]:
c_address_dict

0
0                                  Toronto, ON, Canada
1            45 Parliament Street, Toronto, ON, Canada
2    6205 Rue Vanden Abeele, Saint-Laurent, QC, Canada
3          5300 86 Ave SE, Calgary, AB T2C 2R6, Canada
4        6800 Millcreek Drive, Mississauga, ON, Canada
..                                                 ...
186  415 Saint-Antoine St, Sainte-Anne-de-Bellevue,...
187  5770 Hurontario Street, Mississauga, Ontario L...
188  736 6th Avenue Southwest #875, Calgary, Albert...
189              1540 W 2nd Ave, Vancouver, BC, Canada
190              8 Garamond Court, Toronto, ON, Canada

[191 rows x 1 columns]

In [ ]:
href_dict

0
0    /microsoft-azure-canada-central-toronto
1                    /vantage-qc1-montreal-i
2                                  /ovh-bhs2
3     /core-data-centres-markham-data-centre
4         /cogent-communications-mississauga
..                                       ...
163                    /atos-group-quebec-ii
164                      /atos-group-ontario
165                      /atos-group-alberta
166                /zulu-technology-ltd-dc01
167                       /lumen-dc1-toronto

[168 rows x 1 columns]

Assistance:
When I was trying to collect data for the data centers' certificates, I ran into an error. After looking through the page source, I noticed two problems: 1. the innerhtml was incorrect as it was accessing information from the detail tab rather than the certificate tab. And so, using div_find_element('XPATH of the certificate tab').click() to have it access the html w/ the certificates
2. Checking the new page source, I found out that certificates was stored in a <script tag></script> and so after much google searching, I learned that I needed to use json to webscrape the certificates. Becasue I wasn't quite sure how to do it, I relied on AI (Deepseek) for assistance. As for retrieving all other information, I relied on the code from lecture notes.

NOTE- This was done on all 3 countries(UK, Germany, Canada) as the code to retrieve the data centers' info are all the same. Except for a few name changes, this is for Canada is the exact same code for UK and Germany

Previous code prior to AI assistance where I was using the certicate code from the lecture notes. :



dc_link = []
for link in href_collection:
  url_link = 'https://www.datacenters.com' + link
  dc_link.append(url_link)
desc_list = []
phone_book = []
c_certification_details = []
c_certification_names = []
c_tech = []
all_c = []
# Initialize Chrome driver
driver = gs.Chrome()

# Iterate through all links
for link in dc_link:
    driver.get(link)

    # Extract description
    try:
        description_1 = driver.find_element(By.XPATH, '//*[@id="contentSummary"]').get_attribute('innerHTML')
        desc_list.append(description_1)
        print(description_1)
    except:
        desc_list.append('Description not found')

    # Extract phone number
    try:
        phone_html = driver.find_element(By.XPATH, '//*[@id="locationsSidebarContactPhone"]').get_attribute('innerHTML')
        phone_soup = BeautifulSoup(phone_html, 'html.parser')
        phone_number = phone_soup.find_all('span')[1].text.strip()
        print(phone_number)
        phone_book.append(phone_number)
    except:
        phone_book.append('Phone not found')

    # Extract facilities
    facilities = []
    try:
        inner_html = driver.find_element(By.XPATH, '//*[@id="contentFacilities"]').get_attribute('innerHTML')
        inner_soup = BeautifulSoup(inner_html, 'html.parser')

        for facility in inner_soup.find_all('div', class_='LocationShowContentFacilities__facilityType__kIwxN'):
          name_tag = facility.find('div', class_='LocationShowContentFacilities__facilityName__sTcmQ')
          name = name_tag.text.strip() if name_tag else 'Unknown'
          active = facility.find('div', class_='LocationShowContentFacilities__active__IO6dh')
          status = 'Active' if active else 'Inactive'
          facilities.append({'Name': name, 'Status': status})
        all_c.append(facilities)
    except:
        facilities.append({'Name': 'No facilities found', 'Status': 'N/A'})

    # Print the extracted facilities for the current link
    for f in facilities:
        print(f"Facility: {f['Name']}, Status: {f['Status']}")

    # Extract certifications
    try:
        certifications = inner_soup.find_all('div', class_='LocationShowContentCertifications__certification__yF4qV')
        certification_details = []
        for cert in certifications:
          certification_details = certification_details + [cert.find('div', class_='LocationShowContentCertifications__certificationLabelContainer__wFCGN').text ]
          c_certification_details.append(certification_details)
        certification_names = []
        for cert in certifications:
          c_certification_names = certification_names + [cert.get('id')]
          c_certification_names.append(certification_names)
    except:
        certification_details.append('No certification found')
        certification_names.append('No ID found')
    try:
      tech_specs_html = driver.find_element(By.XPATH, '//*[@id="locationsSidebarStats"]').get_attribute('innerHTML')
      tech_specs_soup = BeautifulSoup(tech_specs_html)
      tech_specs_soup_list = tech_specs_soup.find_all('div', {'class': 'LocationShowSidebarStat__statContainer__LPgsu'})
      tech_spec_dict = dict()
      for tech_spec_soup_single in tech_specs_soup_list:
        tech_spec_dict[tech_spec_soup_single.find('title').text] = tech_spec_soup_single.find('div', {'id': 'statInfo'}).text
      c_tech.append(tech_spec_dict)
    except:
       print("nothing")

# Close the driver after the loop
driver.quit()


In [ ]:
dc_link = []
for link in href_collection:
  url_link = 'https://www.datacenters.com' + link
  dc_link.append(url_link)

desc_list = []
phone_book = []
all_certificates = []
c_tech = []
all_c = []
# Initialize Chrome driver
driver = gs.Chrome()

# Iterate through all links
for link in dc_link:
    driver.get(link)

    # Extract description
    try:
        description_1 = driver.find_element(By.XPATH, '//*[@id="contentSummary"]').get_attribute('innerHTML')
        desc_list.append(description_1)
        print(description_1)
    except:
        desc_list.append('Description not found')

    # Extract phone number
    try:
        phone_html = driver.find_element(By.XPATH, '//*[@id="locationsSidebarContactPhone"]').get_attribute('innerHTML')
        phone_soup = BeautifulSoup(phone_html, 'html.parser')
        phone_number = phone_soup.find_all('span')[1].text.strip()
        print(phone_number)
        phone_book.append(phone_number)
    except:
        phone_book.append('Phone not found')

    # Extract facilities
    facilities = []
    try:
        inner_html = driver.find_element(By.XPATH, '//*[@id="contentFacilities"]').get_attribute('innerHTML')
        inner_soup = BeautifulSoup(inner_html, 'html.parser')

        for facility in inner_soup.find_all('div', class_='LocationShowContentFacilities__facilityType__kIwxN'):
          name_tag = facility.find('div', class_='LocationShowContentFacilities__facilityName__sTcmQ')
          name = name_tag.text.strip() if name_tag else 'Unknown'
          active = facility.find('div', class_='LocationShowContentFacilities__active__IO6dh')
          status = 'Active' if active else 'Inactive'
          facilities.append({'Name': name, 'Status': status})
        all_c.append(facilities)
    except:
        facilities.append({'Name': 'No facilities found', 'Status': 'N/A'})

    # Print the extracted facilities for the current link
    for f in facilities:
        print(f"Facility: {f['Name']}, Status: {f['Status']}")

    # Extract certifications
    try:
        json_data_element = driver.find_element(By.XPATH, '//*[@data-component-name="LocationShow"]')
        json_data_str = json_data_element.get_attribute("innerHTML")
        json_data_str = json_data_element.get_attribute("innerHTML")
        data = json.loads(json_data_str)
        location_data = data.get("location", None)
        certifications_list = []
        if location_data:
          certifications = location_data.get("certifications", [])
          if certifications:
            for cert in certifications:
              certification = {
                "Abbreviation": cert.get("abbreviation", "N/A"),
                "Summary": cert.get("summary", "N/A")
              }
              certifications_list.append(certification)
        print(certifications_list)
        all_certificates.append(certifications_list)
    except:
        print('Nothing')

    try:
      tech_specs_html = driver.find_element(By.XPATH, '//*[@id="locationsSidebarStats"]').get_attribute('innerHTML')
      tech_specs_soup = BeautifulSoup(tech_specs_html)
      tech_specs_soup_list = tech_specs_soup.find_all('div', {'class': 'LocationShowSidebarStat__statContainer__LPgsu'})
      tech_spec_dict = dict()
      for tech_spec_soup_single in tech_specs_soup_list:
        tech_spec_dict[tech_spec_soup_single.find('title').text] = tech_spec_soup_single.find('div', {'id': 'statInfo'}).text
      c_tech.append(tech_spec_dict)
    except:
       print("nothing")

# Close the driver after the loop
driver.quit()


<IPython.core.display.Javascript object>

Microsoft Azure Canada Central-Toronto is located at Toronto, ON, Canada. The gross building size for this location has not been provided. The gross colocation space is not available for this data center. No power information has been offered for this location. We found 98 data center locations within 50 miles of this facility. Certifications for this location include ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC 1, SOC 2, SOC 3.
+1 833-538-1100
Facility: Bare Metal, Status: Inactive
Facility: Internet Exchange, Status: Inactive
Facility: IaaS, Status: Active
Facility: Colocation, Status: Active
[{'Abbreviation': 'ISO 22301', 'Summary': 'ISO 22301 is the international standard for Business Continuity Management (BCM). It provides a practical framework for setting up and managing an effective business continuity management system.'}, {'Abbreviation': 'ISO 27001', 'Summary': "ISO/IEC 27001 is the world's best-known standard for information security management systems (ISMS)."}, {'Abbrevia

In [ ]:
dfcert = pd.DataFrame(all_certificates)
dfcert

0   \
0    {'Abbreviation': 'ISO 22301', 'Summary': 'ISO ...   
1    {'Abbreviation': 'ISO 27001', 'Summary': 'ISO/...   
2    {'Abbreviation': 'HIPAA', 'Summary': 'The Heal...   
3    {'Abbreviation': 'PCI DSS', 'Summary': 'The Pa...   
4                                                 None   
..                                                 ...   
163  {'Abbreviation': 'ISO 22301', 'Summary': 'ISO ...   
164  {'Abbreviation': 'ISO 14001', 'Summary': 'ISO ...   
165  {'Abbreviation': 'ISO 27001', 'Summary': 'ISO/...   
166                                               None   
167  {'Abbreviation': 'HIPAA', 'Summary': 'The Heal...   

                                                    1   \
0    {'Abbreviation': 'ISO 27001', 'Summary': 'ISO/...   
1    {'Abbreviation': 'PCI DSS', 'Summary': 'The Pa...   
2    {'Abbreviation': 'HITECH', 'Summary': 'The Hea...   
3    {'Abbreviation': 'SOC 2 Type 2', 'Summary': 'S...   
4                                                 None   
..                                                 ...   
163  {'Abbreviation': 'ISO 27001', 'Summary': 'ISO/...   
164  {'Abbreviation': 'ISO 22301', 'Summary': 'ISO ...   
165  {'Abbreviation': 'PCI DSS', 'Summary': 'The Pa...   
166                                               None   
167  {'Abbreviation': 'ISO 27001', 'Summary': 'ISO/...   

                                                    2   \
0    {'Abbreviation': 'ISO 9001', 'Summary': 'ISO 9...   
1    {'Abbreviation': 'SOC 2', 'Summary': 'SOC 2 is...   
2    {'Abbreviation': 'ISO 14001', 'Summary': 'ISO ...   
3                                                 None   
4                                                 None   
..                                                 ...   
163  {'Abbreviation': 'ISO/IEC 20000', 'Summary': '...   
164  {'Abbreviation': 'ISO 27001', 'Summary': 'ISO/...   
165  {'Abbreviation': 'SOC 2', 'Summary': 'SOC 2 is...   
166                                               None   
167  {'Abbreviation': 'PCI DSS', 'Summary': 'The Pa...   

                                                    3   \
0    {'Abbreviation': 'PCI DSS', 'Summary': 'The Pa...   
1                                                 None   
2    {'Abbreviation': 'ISO 27001', 'Summary': 'ISO/...   
3                                                 None   
4                                                 None   
..                                                 ...   
163  {'Abbreviation': 'SOC 2', 'Summary': 'SOC 2 is...   
164  {'Abbreviation': 'SOC 2', 'Summary': 'SOC 2 is...   
165                                               None   
166                                               None   
167  {'Abbreviation': 'SOC 1', 'Summary': 'System a...   

                                                    4   \
0    {'Abbreviation': 'SOC 1', 'Summary': 'System a...   
1                                                 None   
2    {'Abbreviation': 'ISO 50001', 'Summary': 'ISO ...   
3                                                 None   
4                                                 None   
..                                                 ...   
163                                               None   
164                                               None   
165                                               None   
166                                               None   
167  {'Abbreviation': 'SOC 2', 'Summary': 'SOC 2 is...   

                                                    5   \
0    {'Abbreviation': 'SOC 2', 'Summary': 'SOC 2 is...   
1                                                 None   
2    {'Abbreviation': 'PCI DSS', 'Summary': 'The Pa...   
3                                                 None   
4                                                 None   
..                                                 ...   
163                                               None   
164                                               None   
165                                          

In [ ]:
all_certificates

[[{'Abbreviation': 'ISO 22301',
   'Summary': 'ISO 22301 is the international standard for Business Continuity Management (BCM). It provides a practical framework for setting up and managing an effective business continuity management system.'},
  {'Abbreviation': 'ISO 27001',
   'Summary': "ISO/IEC 27001 is the world's best-known standard for information security management systems (ISMS)."},
  {'Abbreviation': 'ISO 9001',
   'Summary': 'ISO 9001 sets out the criteria for a quality management system. This standard is based on a number of quality management principles including a strong customer focus, the motivation and implication of top management, the process approach and continual improvement.'},
  {'Abbreviation': 'PCI DSS',
   'Summary': 'The Payment Card Industry Data Security Standard (PCI DSS) is an information security standard used to handle credit cards from major card brands.'},
  {'Abbreviation': 'SOC 1',
   'Summary': "System and Organization Controls 1, or SOC 1, aims 

In [ ]:
c_cert = []
for index, row in enumerate(all_certificates):
  if not row:
    c_cert.append({'Index':index})
  for cell in row:
    cell['Index'] = index
    c_cert.append(cell)
c_cert_df = pd.DataFrame(c_cert)
c_cert_df

Abbreviation                                            Summary  Index
0         ISO 22301  ISO 22301 is the international standard for Bu...      0
1         ISO 27001  ISO/IEC 27001 is the world's best-known standa...      0
2          ISO 9001  ISO 9001 sets out the criteria for a quality m...      0
3           PCI DSS  The Payment Card Industry Data Security Standa...      0
4             SOC 1  System and Organization Controls 1, or SOC 1, ...      0
..              ...                                                ...    ...
432       ISO 27001  ISO/IEC 27001 is the world's best-known standa...    167
433         PCI DSS  The Payment Card Industry Data Security Standa...    167
434           SOC 1  System and Organization Controls 1, or SOC 1, ...    167
435           SOC 2  SOC 2 is an auditing procedure that ensures yo...    167
436  SSAE 16 Type 1  The SSAE 16 audit will result in a Service Org...    167

[437 rows x 3 columns]

In [ ]:
c_cert_df = c_cert_df.groupby('Index').aggregate(list)
c_cert_df

Abbreviation  \
Index                                                      
0      [ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC ...   
1                            [ISO 27001, PCI DSS, SOC 2]   
2      [HIPAA, HITECH, ISO 14001, ISO 27001, ISO 5000...   
3                                [PCI DSS, SOC 2 Type 2]   
4                                                  [nan]   
...                                                  ...   
163         [ISO 22301, ISO 27001, ISO/IEC 20000, SOC 2]   
164             [ISO 14001, ISO 22301, ISO 27001, SOC 2]   
165                          [ISO 27001, PCI DSS, SOC 2]   
166                                                [nan]   
167    [HIPAA, ISO 27001, PCI DSS, SOC 1, SOC 2, SSAE...   

                                                 Summary  
Index                                                     
0      [ISO 22301 is the international standard for B...  
1      [ISO/IEC 27001 is the world's best-known stand...  
2      [The Health Insurance Portability and Accounta...  
3      [The Payment Card Industry Data Security Stand...  
4                                                  [nan]  
...                                                  ...  
163    [ISO 22301 is the international standard for B...  
164    [ISO 14001 is an internationally agreed standa...  
165    [ISO/IEC 27001 is the world's best-known stand...  
166                                                [nan]  
167    [The Health Insurance Portability and Accounta...  

[168 rows x 2 columns]

Google searched/AI searched for function that handles the individual dictionaries in each cell (of the row and column). The goal is to create a dataframe where the columns is the name of the facilities (name key and value in the dictionary) and cell with have the value of status active/inactive.
df.applymap(lambda x: x['Status'])

Initial idea but rejected it later as it's not want I wanted:
cname = []
cstatus = []
for index, row in enumerate(all_c):
  for cell in row:
    cname['Index'] = index
    cstatus['Index'] = index
    cname.append(cell['Name'])
    cstatus.append(cell['Status'])
cnamedf = pd.DataFrame(cname)
cstatusdf = pd.DataFrame(cstatus)
cfac_df = pd.merge(cnamedf, cstatusdf, left_index=True, right_index='Index')

In [ ]:
df = pd.DataFrame(all_c)
status_df = df.applymap(lambda x: x['Status'])
status_df = status_df.rename(columns={ 0:'Bare Metal',1:'IaaS', 2:'Internet Exchange', 3:'Colocation'})
tech_df = pd.DataFrame(c_tech)

<ipython-input-36-4d1add83c8a2>:2: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  status_df = df.applymap(lambda x: x['Status'])


In [ ]:
status_df

Bare Metal      IaaS Internet Exchange Colocation
0     Inactive  Inactive            Active     Active
1     Inactive  Inactive            Active     Active
2     Inactive  Inactive            Active     Active
3       Active  Inactive            Active     Active
4     Inactive  Inactive            Active     Active
..         ...       ...               ...        ...
163   Inactive  Inactive          Inactive   Inactive
164   Inactive  Inactive          Inactive   Inactive
165   Inactive    Active          Inactive   Inactive
166   Inactive    Active          Inactive   Inactive
167     Active    Active          Inactive   Inactive

[168 rows x 4 columns]

In [ ]:
urlTwo = 'https://www.datacenters.com/locations/united-kingdom'
reponseTwo = requests.get(urlTwo)
reponseTwo.text

'\n<!DOCTYPE html>\n<html>\n  <head>\n    <meta name="viewport" content="width=device-width, initial-scale=1.0">\n    <title>United Kingdom Data Centers - Providers Map in United Kingdom</title>\n    <meta name="description" content="Data Centers in United Kingdom with map. List of available providers and facilities in United Kingdom, including Colocation, Bare Metal Servers, and IaaS Data Centers.">\n    <!-- See https://www.abuseipdb.com/ -->\n    <meta name="abuseipdb-verification" content="DRUAmm7d" />\n\n        <!-- OneTrust Cookies Consent Notice start for datacenters.com -->\n  <script src="https://cdn.cookielaw.org/scripttemplates/otSDKStub.js"  type="text/javascript" charset="UTF-8" data-domain-script="c27244d4-b08b-4f0a-8fea-93f49234c91a" ></script>\n  <script type="text/javascript">\n    function OptanonWrapper() { }\n  </script>\n  <!-- OneTrust Cookies Consent Notice end for datacenters.com -->\n\n\n    <script>\n  window.RAILS_ENV = \'production\';\n  window.GA_TID = \'U

In [ ]:
drivertwo = gs.Chrome()
drivertwo.get(urlTwo)


<IPython.core.display.Javascript object>

In [ ]:
drivertwo.page_source

'<html><head>\n    <meta name="viewport" content="width=device-width, initial-scale=1.0">\n    <title>United Kingdom Data Centers - Providers Map in United Kingdom</title>\n    <meta name="description" content="Data Centers in United Kingdom with map. List of available providers and facilities in United Kingdom, including Colocation, Bare Metal Servers, and IaaS Data Centers.">\n    <!-- See https://www.abuseipdb.com/ -->\n    <meta name="abuseipdb-verification" content="DRUAmm7d">\n\n        <!-- OneTrust Cookies Consent Notice start for datacenters.com -->\n  <script async="" src="https://www.googletagmanager.com/gtm.js?id=GTM-KL6NZ94&amp;gtm_auth=2BbtG33W87IQEfI0Hj-ZYw&amp;gtm_preview=env-2&amp;gtm_cookies_win=x"></script><script async="" src="https://www.google-analytics.com/analytics.js"></script><script async="" src="https://www.google-analytics.com/analytics.js"></script><script async="" src="https://www.google-analytics.com/analytics.js"></script><script async="" src="https://w

In [ ]:
second_collection = []
uk_name_collection = []
uk_address_collection = []
while True:
    # Extract inner HTML of the data center container
    uk_dataCenter = drivertwo.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div[2]/div[3]').get_attribute('innerHTML')
    uk_dataCenter_soup = BeautifulSoup(uk_dataCenter, 'html.parser')

    # Find all links with the specified class
    link_list2 = uk_dataCenter_soup.find_all('a', {'class': 'flex flex-col gap-2 rounded border border-gray-100 p-2 hover:border-teal-300 hover:shadow-lg hover:shadow-teal-600/40'})
    nameTwo_list = uk_dataCenter_soup.find_all('div', {'class': 'text font-medium hover:text-purple'})
    addressTwo_list = uk_dataCenter_soup.find_all('div', {'class': 'text-xs text-gray-500'})
    # Collect hrefs
    for a in link_list2:
        if 'href' in a.attrs:
            second_collection.append(a["href"])
    for name in nameTwo_list:
      uk_name_collection.append(name.text)
    for div in addressTwo_list:
      prev_sibling = div.find_previous_sibling('div', {'class': 'text font-medium hover:text-purple'})
      if prev_sibling:
        address = div.text.strip()
        uk_address_collection.append(address)
    # Try to find and click the next button
    try:
      next_button = drivertwo.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div[2]/div[3]/div[2]/div[1]/nav/button[5]')
      next_button.click()
    except Exception as e:
      try:
        next_button = drivertwo.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div[2]/div[3]/div[2]/div[1]/nav/button[8]')
        next_button.click()
      except:
        try:
          next_button = drivertwo.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div[2]/div[3]/div[2]/div[1]/nav/button[9]')
          next_button.click()
        except:
          print(f'No more pages to navigate.{e}')
          break
    print(len(second_collection))
    time.sleep(3)
drivertwo.quit()
second_dict = pd.DataFrame(second_collection)
uk_name_dict = pd.DataFrame(uk_name_collection)
uk_address_dict = pd.DataFrame(uk_address_collection)

6
43
83
123
No more pages to navigate.Message: element click intercepted: Element <button class="Control__control__ijHLR Pagination__pageItem__NsQSw Pagination__disabled__FbUC6 Pagination__symbol__KHv6r" type="button">...</button> is not clickable at point (226, 421). Other element would receive the click: <nav>...</nav>
  (Session info: chrome=135.0.7049.95)
Stacktrace:
#0 0x58a865f97cea <unknown>
#1 0x58a865a485f0 <unknown>
#2 0x58a865aa087c <unknown>
#3 0x58a865a9e6dc <unknown>
#4 0x58a865a9bd72 <unknown>
#5 0x58a865a9b467 <unknown>
#6 0x58a865a8db3d <unknown>
#7 0x58a865abf662 <unknown>
#8 0x58a865a8d4ba <unknown>
#9 0x58a865abf82e <unknown>
#10 0x58a865ae5660 <unknown>
#11 0x58a865abf433 <unknown>
#12 0x58a865a8bea3 <unknown>
#13 0x58a865a8cb01 <unknown>
#14 0x58a865f5cb3b <unknown>
#15 0x58a865f60a21 <unknown>
#16 0x58a865f43c32 <unknown>
#17 0x58a865f61594 <unknown>
#18 0x58a865f27eef <unknown>
#19 0x58a865f85d98 <unknown>
#20 0x58a865f85f76 <unknown>
#21 0x58a865f96b36 <unknown

In [ ]:
uk_address_dict

0
0                  Harbour Exchange Square, London, UK
1                 1 Banbury Avenue, Slough SL1 4LH, UK
2                      8 Buckingham Avenue, Slough, UK
3                    352 Buckingham Avenue, Slough, UK
4     Powergate Business Park, Volt Avenue, London, UK
..                                                 ...
192             Crewe Hall Farm, Haslington, Crewe, UK
193  Beeston Business, Technology Drive, Beeston, N...
194  110 Birchwood Boulevard, Birchwood, Warrington...
195  Westlakes Science Park, Ingwell Drive, Moor Ro...
196                   23 West Nile Street, Glasgow, UK

[197 rows x 1 columns]

In [ ]:
second_dict

0
0    /microsoft-azure-uk-south-london
1    /microsoft-azure-uk-west-cardiff
2                  /amazon-aws-didcot
3                /verne-global-london
4                /ntt-global-london-1
..                                ...
155                 /atos-group-crewe
156            /atos-group-nottingham
157            /atos-group-warrington
158            /atos-group-whitehaven
159     /lumen-glasgow-north-london-1

[160 rows x 1 columns]

Tried several times to get all 260 data centers from Canada but was unsuccessful -> the code managed to get everything for UK and Germany though

In [ ]:
uk_dc_link = []
for link in second_collection:
    url_link = 'https://www.datacenters.com' + link
    uk_dc_link.append(url_link)

# Initialize data lists
uk_desc_list = []
uk_phone_book = []
uk_certificates = []
uk_tech = []
all_uk = []
# Start Chrome driver
drivertwo = gs.Chrome()

# Iterate through all UK datacenter links
for link in uk_dc_link:
    drivertwo.get(link)
    time.sleep(3)  # Allow page to load fully

    # Extract description
    try:
        uk_description_1 = drivertwo.find_element(By.XPATH, '//*[@id="contentSummary"]').get_attribute('innerHTML')
        uk_desc_list.append(uk_description_1.strip())
        print(f"Description: {uk_description_1.strip()}")
    except:
        uk_desc_list.append('Description not found')
        print("Description not found")

    # Extract phone number
    try:
        uk_phone_html = drivertwo.find_element(By.XPATH, '//*[@id="locationsSidebarContactPhone"]').get_attribute('innerHTML')
        uk_phone_soup = BeautifulSoup(uk_phone_html, 'html.parser')
        uk_phone_number = uk_phone_soup.find_all('span')[1].text.strip()
        uk_phone_book.append(uk_phone_number)
        print(f"Phone: {uk_phone_number}")
    except:
        uk_phone_book.append('Phone not found')
        print("Phone not found")

    # Extract facilities
    uk_facilities = []  # Reset facility list for each link
    try:
        uk_inner_html = drivertwo.find_element(By.XPATH, '//*[@id="contentFacilities"]').get_attribute('innerHTML')
        uk_inner_soup = BeautifulSoup(uk_inner_html, 'html.parser')

        for facility in uk_inner_soup.find_all('div', class_='LocationShowContentFacilities__facilityType__kIwxN'):
          uk_name_tag = facility.find('div', class_='LocationShowContentFacilities__facilityName__sTcmQ')
          uk_name = uk_name_tag.text.strip() if uk_name_tag else 'Unknown'
          uk_active = facility.find('div', class_='LocationShowContentFacilities__active__IO6dh')
          uk_status = 'Active' if uk_active else 'Inactive'
          uk_facilities.append({'Name': uk_name, 'Status': uk_status})
        all_uk.append(uk_facilities)
        # Print the extracted facilities for the current link
        for f in uk_facilities:
            print(f"Facility: {f['Name']}, Status: {f['Status']}")
    except:
        uk_facilities.append({'Name': 'No facilities found', 'Status': 'N/A'})
        print("No facilities found")

    # Extract certifications
    try:
        json_data_element = drivertwo.find_element(By.XPATH, '//*[@data-component-name="LocationShow"]')
        json_data_str = json_data_element.get_attribute("innerHTML")
        json_data_str = json_data_element.get_attribute("innerHTML")
        data = json.loads(json_data_str)
        location_data = data.get("location", None)
        certifications_list = []
        if location_data:
          certifications = location_data.get("certifications", [])
          if certifications:
            for cert in certifications:
              certification = {
                "Abbreviation": cert.get("abbreviation", "N/A"),
                "Summary": cert.get("summary", "N/A")
              }
              certifications_list.append(certification)
        print(certifications_list)
        uk_certificates.append(certifications_list)
    except:
        print('Nothing')

    # Extract technical specifications
    try:
      tech_specs_html = drivertwo.find_element(By.XPATH, '//*[@id="locationsSidebarStats"]').get_attribute('innerHTML')
      tech_specs_soup = BeautifulSoup(tech_specs_html)
      tech_specs_soup_list = tech_specs_soup.find_all('div', {'class': 'LocationShowSidebarStat__statContainer__LPgsu'})
      tech_spec_dict = dict()
      for tech_spec_soup_single in tech_specs_soup_list:
        tech_spec_dict[tech_spec_soup_single.find('title').text] = tech_spec_soup_single.find('div', {'id': 'statInfo'}).text
      uk_tech.append(tech_spec_dict)
    except:
        print("No technical specs found")

# Close the driver after the loop
drivertwo.quit()


<IPython.core.display.Javascript object>

Description: Microsoft Azure UK South-London is located at London, UK. The gross building size for this location has not been provided. The gross colocation space is not available for this data center. No power information has been offered for this location. We found 196 data center locations within 50 miles of this facility. Certifications for this location include ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC 1, SOC 2, SOC 3.
Phone: +1 833-538-1100
Facility: Bare Metal, Status: Inactive
Facility: Internet Exchange, Status: Inactive
Facility: IaaS, Status: Active
Facility: Colocation, Status: Active
[{'Abbreviation': 'ISO 22301', 'Summary': 'ISO 22301 is the international standard for Business Continuity Management (BCM). It provides a practical framework for setting up and managing an effective business continuity management system.'}, {'Abbreviation': 'ISO 27001', 'Summary': "ISO/IEC 27001 is the world's best-known standard for information security management systems (ISMS)."}, {'Abb

In [ ]:
uk_cert = []
for index, row in enumerate(uk_certificates):
  if not row:
    uk_cert.append({'Index':index})
  for cell in row:
    cell['Index'] = index
    uk_cert.append(cell)
uk_cert_df = pd.DataFrame(uk_cert)
uk_cert_df

Abbreviation                                            Summary  Index
0         ISO 22301  ISO 22301 is the international standard for Bu...      0
1         ISO 27001  ISO/IEC 27001 is the world's best-known standa...      0
2          ISO 9001  ISO 9001 sets out the criteria for a quality m...      0
3           PCI DSS  The Payment Card Industry Data Security Standa...      0
4             SOC 1  System and Organization Controls 1, or SOC 1, ...      0
..              ...                                                ...    ...
556         PCI DSS  The Payment Card Industry Data Security Standa...    159
557           SOC 1  System and Organization Controls 1, or SOC 1, ...    159
558           SOC 2  SOC 2 is an auditing procedure that ensures yo...    159
559  SSAE 16 Type 1  The SSAE 16 audit will result in a Service Org...    159
560  SSAE 16 Type 2  The SSAE 16 audit will result in a Service Org...    159

[561 rows x 3 columns]

In [ ]:
uk_cert_df = uk_cert_df.groupby('Index').aggregate(list)
uk_cert_df

Abbreviation  \
Index                                                      
0      [ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC ...   
1      [ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC ...   
2      [ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC ...   
3       [HIPAA, ISO 14001, ISO 27001, ISO 9001, PCI DSS]   
4      [ISAE-3402, ISO 14001, ISO 22301, ISO 27001, I...   
...                                                  ...   
155                [ISO 22301, ISO 27001, ISO/IEC 20000]   
156                                                [nan]   
157                                                [nan]   
158                                                [nan]   
159    [HIPAA, ISO 27001, PCI DSS, SOC 1, SOC 2, SSAE...   

                                                 Summary  
Index                                                     
0      [ISO 22301 is the international standard for B...  
1      [ISO 22301 is the international standard for B...  
2      [ISO 22301 is the international standard for B...  
3      [The Health Insurance Portability and Accounta...  
4      [ISAE 3402 was developed to provide an interna...  
...                                                  ...  
155    [ISO 22301 is the international standard for B...  
156                                                [nan]  
157                                                [nan]  
158                                                [nan]  
159    [The Health Insurance Portability and Accounta...  

[160 rows x 2 columns]

In [ ]:
ukdf = pd.DataFrame(all_uk)
ukstatus_df = ukdf.applymap(lambda x: x['Status'])
ukstatus_df = ukstatus_df.rename(columns={ 0:'Bare Metal',1:'IaaS', 2:'Internet Exchange', 3:'Colocation'})
uktech_df = pd.DataFrame(uk_tech)

<ipython-input-57-86c3ad2a9889>:2: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  ukstatus_df = ukdf.applymap(lambda x: x['Status'])


In [ ]:
urlThree = "https://www.datacenters.com/locations/germany"
responseThree = requests.get(urlThree)
responseThree.text

'\n<!DOCTYPE html>\n<html>\n  <head>\n    <meta name="viewport" content="width=device-width, initial-scale=1.0">\n    <title>Germany Data Centers - Providers Map in Germany</title>\n    <meta name="description" content="Data Centers in Germany with map. List of available providers and facilities in Germany, including Colocation, Bare Metal Servers, and IaaS Data Centers.">\n    <!-- See https://www.abuseipdb.com/ -->\n    <meta name="abuseipdb-verification" content="DRUAmm7d" />\n\n        <!-- OneTrust Cookies Consent Notice start for datacenters.com -->\n  <script src="https://cdn.cookielaw.org/scripttemplates/otSDKStub.js"  type="text/javascript" charset="UTF-8" data-domain-script="c27244d4-b08b-4f0a-8fea-93f49234c91a" ></script>\n  <script type="text/javascript">\n    function OptanonWrapper() { }\n  </script>\n  <!-- OneTrust Cookies Consent Notice end for datacenters.com -->\n\n\n    <script>\n  window.RAILS_ENV = \'production\';\n  window.GA_TID = \'UA-46812924-1\';\n    window.

In [ ]:
driverthree = gs.Chrome()
driverthree.get(urlThree)

<IPython.core.display.Javascript object>

In [ ]:
driverthree.page_source

'<html><head>\n    <meta name="viewport" content="width=device-width, initial-scale=1.0">\n    <title>Germany Data Centers - Providers Map in Germany</title>\n    <meta name="description" content="Data Centers in Germany with map. List of available providers and facilities in Germany, including Colocation, Bare Metal Servers, and IaaS Data Centers.">\n    <!-- See https://www.abuseipdb.com/ -->\n    <meta name="abuseipdb-verification" content="DRUAmm7d">\n\n        <!-- OneTrust Cookies Consent Notice start for datacenters.com -->\n  <script async="" src="https://www.googletagmanager.com/gtm.js?id=GTM-KL6NZ94&amp;gtm_auth=2BbtG33W87IQEfI0Hj-ZYw&amp;gtm_preview=env-2&amp;gtm_cookies_win=x"></script><script async="" src="https://www.google-analytics.com/analytics.js"></script><script async="" src="https://www.google-analytics.com/analytics.js"></script><script async="" src="https://www.google-analytics.com/analytics.js"></script><script async="" src="https://www.google-analytics.com/anal

In [ ]:
third_collection = []
g_name_collection = []
g_address_collection = []
while True:
    # Extract inner HTML of the data center container
    g_dataCenter = driverthree.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div[2]/div[3]').get_attribute('innerHTML')
    g_dataCenter_soup = BeautifulSoup(g_dataCenter, 'html.parser')

    # Find all links with the specified class
    link_list = g_dataCenter_soup.find_all('a', {'class': 'flex flex-col gap-2 rounded border border-gray-100 p-2 hover:border-teal-300 hover:shadow-lg hover:shadow-teal-600/40'})
    nameThree_list = g_dataCenter_soup.find_all('div', {'class': 'text font-medium hover:text-purple'})
    addressThree_list = g_dataCenter_soup.find_all('div', {'class': 'text-xs text-gray-500'})

    for div in addressThree_list:
      prev_sibling = div.find_previous_sibling('div', {'class': 'text font-medium hover:text-purple'})
      if prev_sibling:
        address = div.text.strip()
        g_address_collection.append(address)
    for name in nameThree_list:
      g_name_collection.append(name.text)
    # Collect hrefs
    for a in link_list:
        if 'href' in a.attrs:
            third_collection.append(a["href"])

    # Try to find and click the next button
    try:
      next_button = driverthree.find_element(By.XPATH, '/html/body/div[1]/div[4]/div/div[2]/div[3]/div[2]/div[1]/nav/button[5]')
      next_button.click()
      time.sleep(3)
    except Exception as e:
        print(f'No more pages to navigate.{e}')
        break
driverthree.quit()
third_dict = pd.DataFrame(third_collection)
g_address_dict = pd.DataFrame(g_address_collection)
g_name_dict = pd.DataFrame(g_name_collection)

No more pages to navigate.Message: element click intercepted: Element <button class="Control__control__ijHLR Pagination__pageItem__NsQSw Pagination__disabled__FbUC6 Pagination__symbol__KHv6r" type="button">...</button> is not clickable at point (227, 421). Other element would receive the click: <nav>...</nav>
  (Session info: chrome=135.0.7049.95)
Stacktrace:
#0 0x5be175750cea <unknown>
#1 0x5be1752015f0 <unknown>
#2 0x5be17525987c <unknown>
#3 0x5be1752576dc <unknown>
#4 0x5be175254d72 <unknown>
#5 0x5be175254467 <unknown>
#6 0x5be175246b3d <unknown>
#7 0x5be175278662 <unknown>
#8 0x5be1752464ba <unknown>
#9 0x5be17527882e <unknown>
#10 0x5be17529e660 <unknown>
#11 0x5be175278433 <unknown>
#12 0x5be175244ea3 <unknown>
#13 0x5be175245b01 <unknown>
#14 0x5be175715b3b <unknown>
#15 0x5be175719a21 <unknown>
#16 0x5be1756fcc32 <unknown>
#17 0x5be17571a594 <unknown>
#18 0x5be1756e0eef <unknown>
#19 0x5be17573ed98 <unknown>
#20 0x5be17573ef76 <unknown>
#21 0x5be17574fb36 <unknown>
#22 0x7bbb

In [ ]:
third_dict

0
0                                  /amazon-aws-fra54
1    /microsoft-azure-germany-west-central-frankfurt
2                          /hetzner-park-falkenstein
3             /oracle-germany-central-eu-frankfurt-1
4                                  /amazon-aws-fra52
..                                               ...
169                               /centerserv-bremen
170                         /zenlayer-fra3-frankfurt
171                              /atos-group-germany
172                     /lumen-berlin-kitzingstrasse
173                       /lumen-berlin-gradestrasse

[174 rows x 1 columns]

In [ ]:
g_name_dict

0
0                                  FRA54
1         Germany West Central-Frankfurt
2              FR2 Frankfurt Data Center
3              FR5 Frankfurt Data Center
4    FR4 Frankfurt-Griesheim Data Center
..                                   ...
208                   Bremen Data Center
209           FRA3 Frankfurt Data Center
210                  Germany Data Center
211     Berlin Kitzingstraße Data Center
212       Berlin Gradestraße Data Center

[213 rows x 1 columns]

In [ ]:
g_address_dict

0
0    Eschborner Landstraße 100, 60489 Frankfurt am ...
1                           Frankfurt am Main, Germany
2              Kruppstraße 121-127, Frankfurt, Germany
3                  Kleyerstraße 90, Frankfurt, Germany
4                Lärchenstraße 110, Frankfurt, Germany
..                                                 ...
208  Bremen Airport (BRE), Flughafenallee, Bremen, ...
209  Weismüllerstraße 32-40, 60314 Frankfurt am Mai...
210  Würzburger Str. 121, 90766 Fürth-Unterfarrnbac...
211               Kitzingstraße 15-19, Berlin, Germany
212                    Gradestraße 60, Berlin, Germany

[213 rows x 1 columns]

In [ ]:
g_dc_link = []
for link in third_collection:
    url_link = 'https://www.datacenters.com' + link
    g_dc_link.append(url_link)

g_desc_list = []
g_phone_book = []
g_certificates = []
g_tech = []
all_g = []
# Initialize Chrome driver
driverthree = gs.Chrome()

# Iterate through all links
for link in g_dc_link:
    driverthree.get(link)

    # Extract description
    try:
        description_1 = driverthree.find_element(By.XPATH, '//*[@id="contentSummary"]').get_attribute('innerHTML')
        g_desc_list.append(description_1)
        print(description_1)
    except:
        g_desc_list.append('Description not found')

    # Extract phone number
    try:
        phone_html = driverthree.find_element(By.XPATH, '//*[@id="locationsSidebarContactPhone"]').get_attribute('innerHTML')
        phone_soup = BeautifulSoup(phone_html, 'html.parser')
        phone_number = phone_soup.find_all('span')[1].text.strip()
        print(phone_number)
        g_phone_book.append(phone_number)
    except:
        g_phone_book.append('Phone not found')

    # Get facilities
    g_facilities = []  # Reset facility list for each link
    try:
        inner_html = driverthree.find_element(By.XPATH, '//*[@id="contentFacilities"]').get_attribute('innerHTML')
        inner_soup = BeautifulSoup(inner_html, 'html.parser')

        for facility in inner_soup.find_all('div', class_='LocationShowContentFacilities__facilityType__kIwxN'):
          name_tag = facility.find('div', class_='LocationShowContentFacilities__facilityName__sTcmQ')
          name = name_tag.text.strip() if name_tag else 'Unknown'
          active = facility.find('div', class_='LocationShowContentFacilities__active__IO6dh')
          status = 'Active' if active else 'Inactive'
          g_facilities.append({'Name': name, 'Status': status})
        all_g.append(g_facilities)
    except:
        g_facilities.append({'Name': 'No facilities found', 'Status': 'N/A'})

    # Print the extracted facilities for the current link
    for f in g_facilities:
        print(f"Facility: {f['Name']}, Status: {f['Status']}")

    # Extract certifications
    try:
        json_data_element = driverthree.find_element(By.XPATH, '//*[@data-component-name="LocationShow"]')
        json_data_str = json_data_element.get_attribute("innerHTML")
        json_data_str = json_data_element.get_attribute("innerHTML")
        data = json.loads(json_data_str)
        location_data = data.get("location", None)
        certifications_list = []
        if location_data:
          certifications = location_data.get("certifications", [])
          if certifications:
            for cert in certifications:
              certification = {
                "Abbreviation": cert.get("abbreviation", "N/A"),
                "Summary": cert.get("summary", "N/A")
              }
              certifications_list.append(certification)
        print(certifications_list)
        g_certificates.append(certifications_list)
    except:
        print('Nothing')

    # Extract tech specs
    try:
      tech_specs_html = driverthree.find_element(By.XPATH, '//*[@id="locationsSidebarStats"]').get_attribute('innerHTML')
      tech_specs_soup = BeautifulSoup(tech_specs_html)
      tech_specs_soup_list = tech_specs_soup.find_all('div', {'class': 'LocationShowSidebarStat__statContainer__LPgsu'})
      tech_spec_dict = dict()
      for tech_spec_soup_single in tech_specs_soup_list:
        tech_spec_dict[tech_spec_soup_single.find('title').text] = tech_spec_soup_single.find('div', {'id': 'statInfo'}).text
      g_tech.append(tech_spec_dict)
    except:
        print("No tech specs found")

# Close the driver after the loop
driverthree.quit()


<IPython.core.display.Javascript object>

Amazon AWS FRA54 is located at Eschborner Landstraße 100, 60489 Frankfurt am Main, Germany. The gross building size for this location has not been provided. The gross colocation space is not available for this data center. No power information has been offered for this location. We found 119 data center locations within 50 miles of this facility. Certifications for this location include ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC 1, SOC 2, SOC 3.
+1 844-902-4700
Facility: Bare Metal, Status: Inactive
Facility: IaaS, Status: Inactive
Facility: Internet Exchange, Status: Inactive
Facility: Colocation, Status: Active
[{'Abbreviation': 'ISO 22301', 'Summary': 'ISO 22301 is the international standard for Business Continuity Management (BCM). It provides a practical framework for setting up and managing an effective business continuity management system.'}, {'Abbreviation': 'ISO 27001', 'Summary': "ISO/IEC 27001 is the world's best-known standard for information security management systems 

In [ ]:
g_cert = []
for index, row in enumerate(g_certificates):
  if not row:
    g_cert.append({'Index':index})
  for cell in row:
    cell['Index'] = index
    g_cert.append(cell)
g_cert_df = pd.DataFrame(g_cert)
g_cert_df

Abbreviation                                            Summary  Index
0         ISO 22301  ISO 22301 is the international standard for Bu...      0
1         ISO 27001  ISO/IEC 27001 is the world's best-known standa...      0
2          ISO 9001  ISO 9001 sets out the criteria for a quality m...      0
3           PCI DSS  The Payment Card Industry Data Security Standa...      0
4             SOC 1  System and Organization Controls 1, or SOC 1, ...      0
..              ...                                                ...    ...
480         PCI DSS  The Payment Card Industry Data Security Standa...    173
481           SOC 1  System and Organization Controls 1, or SOC 1, ...    173
482           SOC 2  SOC 2 is an auditing procedure that ensures yo...    173
483  SSAE 16 Type 1  The SSAE 16 audit will result in a Service Org...    173
484  SSAE 16 Type 2  The SSAE 16 audit will result in a Service Org...    173

[485 rows x 3 columns]

In [ ]:
g_cert_df = g_cert_df.groupby('Index').aggregate(list)
g_cert_df

Abbreviation  \
Index                                                      
0      [ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC ...   
1      [ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC ...   
2                                            [ISO 27001]   
3      [ISO 27001, ISO 9001, ISO/IEC 20000, PCI DSS, ...   
4      [ISO 22301, ISO 27001, ISO 9001, PCI DSS, SOC ...   
...                                                  ...   
169                                                [nan]   
170    [ISO 22301, ISO 27001, ISO 45001, ISO 9001:201...   
171                    [ISO 22301, ISO 27001, ISO 50001]   
172    [HIPAA, ISO 27001, PCI DSS, SOC 1, SOC 2, SSAE...   
173    [HIPAA, ISO 27001, PCI DSS, SOC 1, SOC 2, SSAE...   

                                                 Summary  
Index                                                     
0      [ISO 22301 is the international standard for B...  
1      [ISO 22301 is the international standard for B...  
2      [ISO/IEC 27001 is the world's best-known stand...  
3      [ISO/IEC 27001 is the world's best-known stand...  
4      [ISO 22301 is the international standard for B...  
...                                                  ...  
169                                                [nan]  
170    [ISO 22301 is the international standard for B...  
171    [ISO 22301 is the international standard for B...  
172    [The Health Insurance Portability and Accounta...  
173    [The Health Insurance Portability and Accounta...  

[174 rows x 2 columns]

In [ ]:
gdf = pd.DataFrame(all_g)
gstatus_df = gdf.applymap(lambda x: x['Status'])
gstatus_df = gstatus_df.rename(columns={ 0:'Bare Metal',1:'IaaS', 2:'Internet Exchange', 3:'Colocation'})
gtech_df = pd.DataFrame(g_tech)

<ipython-input-84-d02d8503968e>:2: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  gstatus_df = gdf.applymap(lambda x: x['Status'])


In [ ]:
c_desc_df = pd.DataFrame(desc_list)
c_phone_df = pd.DataFrame(phone_book)
a = pd.merge(c_desc_df, c_phone_df, left_index=True, right_index=True)
x = pd.merge(status_df, tech_df, left_index=True, right_index=True)

uk_desc_df = pd.DataFrame(uk_desc_list)
uk_phone_df = pd.DataFrame(uk_phone_book)
b = pd.merge(uk_desc_df, uk_phone_df, left_index=True, right_index=True)
y = pd.merge(ukstatus_df, uktech_df, left_index=True, right_index=True)

g_desc_df = pd.DataFrame(g_desc_list)
g_phone_df = pd.DataFrame(g_phone_book)
c = pd.merge(g_desc_df, g_phone_df, left_index=True, right_index=True)
z = pd.merge(gstatus_df, gtech_df, left_index=True, right_index=True)

In [ ]:
onedf = pd.merge(c_name_dict, c_address_dict, left_index=True, right_index=True)
twodf = pd.merge(c_name_dict, href_dict, left_index=True, right_index=True)
Canada_df = pd.merge(onedf, twodf, left_index=True, right_index=True)
Canada_df = Canada_df.rename(columns={'0_x_x':'Name', '0_y_x':'Address', '0_y_y':'Href'})
Canada_df = pd.merge(Canada_df, a, left_index=True, right_index=True)
Canada_df = Canada_df.rename(columns={'0_x':'Description', '0_y':'Phone Number'})
Canada_df = pd.merge(Canada_df,x,left_index=True, right_index=True )
## each row will now include a different certificate + its summary description

Canada_df = pd.merge(Canada_df, c_cert_df, left_index=True, right_on='Index')
Canada_df.columns

Index(['Name', 'Address', '0_x_y', 'Href', 'Description', 'Phone Number',
       'Bare Metal', 'IaaS', 'Internet Exchange', 'Colocation_x', 'Products',
       'Airplane', 'Building', 'Colocation_y', 'Power', 'Abbreviation',
       'Summary'],
      dtype='object')

In [ ]:
Canada_df['Country'] = 'Canada'
Canada_df = Canada_df.drop(columns=['0_x_y'])
Canada_df

Name  \
Index                                        
0                   Canada Central-Toronto   
1                 TR2 Toronto Data Centers   
2             MT1 Montreal IBX Data Center   
3              CL3 Calgary IBX Data Center   
4      YYZ1 Mississauga Data Center Campus   
...                                    ...   
163                    Beanfield 23 Fraser   
164                    Toronto Data Center   
165                     Toronto Datacenter   
166              YWG2 Winnipeg Data Center   
167                       Tor1 Data Center   

                                                 Address  \
Index                                                      
0                                    Toronto, ON, Canada   
1              45 Parliament Street, Toronto, ON, Canada   
2      6205 Rue Vanden Abeele, Saint-Laurent, QC, Canada   
3            5300 86 Ave SE, Calgary, AB T2C 2R6, Canada   
4          6800 Millcreek Drive, Mississauga, ON, Canada   
...                                                  ...   
163           23 Fraser Ave, Toronto, ON M6K 1Y7, Canada   
164          20 Pullman Ct, Scarborough, Ontario, Canada   
165    30 Sims Crescent, Richmond Hill, Ontario L4B 2...   
166             294 Portage Avenue, Winnipeg, MB, Canada   
167      151 Front Street West, Toronto, Ontario, Canada   

                                          Href  \
Index                                            
0      /microsoft-azure-canada-central-toronto   
1                      /vantage-qc1-montreal-i   
2                                    /ovh-bhs2   
3       /core-data-centres-markham-data-centre   
4           /cogent-communications-mississauga   
...                                        ...   
163                      /atos-group-quebec-ii   
164                        /atos-group-ontario   
165                        /atos-group-alberta   
166                  /zulu-technology-ltd-dc01   
167                         /lumen-dc1-toronto   

                                             Description     Phone Number  \
Index                                                                       
0      Microsoft Azure Canada Central-Toronto is loca...  +1 833-538-1100   
1      Vantage Data Centers QC1 Montreal I Data Cente...  +1 866-445-9110   
2      OVHCloud BHS2 Data Center is located at 50 Rue...  +1 833-476-4400   
3      CORE Data Centres Markham Data Centre is locat...  +1 877-881-6530   
4      Cogent Communications Mississauga Data Center ...  +1 844-823-6300   
...                                                  ...              ...   
163    Atos Group Quebec Data Center II is located at...  +1 833-456-7700   
164    Atos Group Ontario Data Center is located at 5...  +1 833-456-7700   
165    Atos Group Alberta Data Center is located at 7...  +1 833-456-7700   
166    Zulu Technology Ltd DC01 Data Center is locate...  +1 833-476-4400   
167    Lumen DC1 Toronto Data Center is located at 8 ...  +1 877-881-6530   

      Bare Metal      IaaS Internet Exchange Colocation_x  \
Index                                                       
0       Inactive  Inactive            Active       Active   
1       Inactive  Inactive            Active       Active   
2       Inactive  Inactive            Active       Active   
3         Active  Inactive            Active       Active   
4       Inactive  Inactive            Active       Active   
...          ...       ...               ...          ...   
163     Inactive  Inactive          Inactive     Inactive   
164     Inactive  Inactive          Inactive     Inactive   
165     Inactive    Active          Inactive     Inactive   
166     Inactive    Active          Inactive     Inactive   
167       Active    Active          Inactive     Inactive   

                    Products                         Airplane  \
Index                                                           
0      0 colocation products  224.32 miles to nearest airport   
1      0 colocat

In [ ]:
uk_onedf = pd.merge(uk_name_dict, uk_address_dict, left_index=True, right_index=True)
uk_twodf = pd.merge(uk_name_dict, second_dict, left_index=True, right_index=True)
UK_df = pd.merge(uk_onedf, uk_twodf, left_index=True, right_index=True)
UK_df = UK_df.rename(columns={'0_x_x':'Name', '0_y_x':'Address', '0_y_y':'Href'})
UK_df = pd.merge(UK_df, b, left_index=True, right_index=True)
UK_df = UK_df.rename(columns={'0_x':'Description', '0_y':'Phone Number'})
UK_df = pd.merge(UK_df, y, left_index=True, right_index=True)
## each row will now include a different certificate + its summary description
UK_df = pd.merge(UK_df, uk_cert_df, left_index=True, right_on='Index')
UK_df.columns

Index(['Name', 'Address', '0_x_y', 'Href', 'Description', 'Phone Number',
       'Bare Metal', 'IaaS', 'Internet Exchange', 'Colocation_x', 'Products',
       'Airplane', 'Building', 'Power', 'Colocation_y', 'Abbreviation',
       'Summary'],
      dtype='object')

In [ ]:
UK_df['Country'] = 'United Kingdom'
UK_df = UK_df.drop(columns='0_x_y')
UK_df

Name  \
Index                                    
0               LD8 London Data Center   
1               LD7 London Data Center   
2               LD5 Slough Data Center   
3               LD6 Slough Data Center   
4               LD9 London Data Center   
...                                ...   
155            London LON1 Data Center   
156    Data Centre, The Chess Building   
157                 London Data Center   
158          London LON-01 Data Center   
159                       Croydon LN-1   

                                                 Address  \
Index                                                      
0                    Harbour Exchange Square, London, UK   
1                   1 Banbury Avenue, Slough SL1 4LH, UK   
2                        8 Buckingham Avenue, Slough, UK   
3                      352 Buckingham Avenue, Slough, UK   
4       Powergate Business Park, Volt Avenue, London, UK   
...                                                  ...   
155    240 E India Dock Rd, London E14 9YY, United Ki...   
156    9-17 Caxton Way, Watford WD18 8RH, United Kingdom   
157                110 High Holborn, London WC1V 6JS, UK   
158            Dundee Rd, Slough SL1 4JU, United Kingdom   
159         unit 1, 35 Imperial Way, Croydon CR0 4RL, UK   

                                   Href  \
Index                                     
0      /microsoft-azure-uk-south-london   
1      /microsoft-azure-uk-west-cardiff   
2                    /amazon-aws-didcot   
3                  /verne-global-london   
4                  /ntt-global-london-1   
...                                 ...   
155                   /atos-group-crewe   
156              /atos-group-nottingham   
157              /atos-group-warrington   
158              /atos-group-whitehaven   
159       /lumen-glasgow-north-london-1   

                                             Description     Phone Number  \
Index                                                                       
0      Microsoft Azure UK South-London is located at ...  +1 833-538-1100   
1      Microsoft Azure UK West-Cardiff is located at ...  +1 833-538-1100   
2      Amazon AWS Didcot is located at Didcot OX11 7Y...  +1 844-902-4700   
3      Verne Global London Data Center is located at ...  +1 877-857-4410   
4      NTT Global Data Centers London 1 Data Center i...  +1 833-544-2200   
...                                                  ...              ...   
155    Atos Group Crewe Data Center is located at Cre...  +1 833-456-7700   
156    Atos Group Nottingham Data Center is located a...  +1 833-456-7700   
157    Atos Group Warrington Data Center is located a...  +1 833-456-7700   
158    Atos Group Whitehaven Data Center is located a...  +1 833-456-7700   
159    Lumen Glasgow North London Data Center 1 is lo...  +1 877-881-6530   

      Bare Metal      IaaS Internet Exchange Colocation_x  \
Index                                                       
0       Inactive  Inactive            Active       Active   
1       Inactive  Inactive            Active       Active   
2       Inactive  Inactive          Inactive       Active   
3         Active  Inactive            Active       Active   
4       Inactive    Active          Inactive     Inactive   
...          ...       ...               ...          ...   
155     Inactive  Inactive          Inactive     Inactive   
156     Inactive  Inactive          Inactive     Inactive   
157     Inactive  Inactive          Inactive     Inactive   
158     Inactive  Inactive          Inactive     Inactive   
159       Active    Active          Inactive     Inactive   

                    Products                        Airplane  \
Index                                                          
0      0 colocation products   14.3 miles to nearest airport   
1      0 colocation products  116.2 miles to nearest airport   
2      0 colocation products  36.04 miles to nearest airport   
3      0 colocation products  

In [ ]:
g_onedf = pd.merge(g_name_dict, g_address_dict, left_index=True, right_index=True)
g_twodf = pd.merge(g_name_dict, third_dict, left_index=True, right_index=True)
Germany_df = pd.merge(g_onedf, g_twodf, left_index=True, right_index=True)
Germany_df = Germany_df.rename(columns={'0_x_x':'Name', '0_y_x':'Address', '0_y_y':'Href'})
Germany_df = pd.merge(Germany_df, c, left_index=True, right_index=True)
Germany_df = Germany_df.rename(columns={'0_x':'Description', '0_y':'Phone Number'})
Germany_df = pd.merge(Germany_df, z, left_index=True, right_index=True)
Germany_df = pd.merge(Germany_df, g_cert_df, left_index=True, right_on='Index')
Germany_df.columns

Index(['Name', 'Address', '0_x_y', 'Href', 'Description', 'Phone Number',
       'Bare Metal', 'IaaS', 'Internet Exchange', 'Colocation_x', 'Products',
       'Airplane', 'Building', 'Power', 'Colocation_y', 'Abbreviation',
       'Summary'],
      dtype='object')

In [ ]:
Germany_df['Country'] = 'Germany'
Germany_df = Germany_df.drop(columns=['0_x_y'])
Germany_df

Name  \
Index                                        
0                                    FRA54   
1           Germany West Central-Frankfurt   
2                FR2 Frankfurt Data Center   
3                FR5 Frankfurt Data Center   
4      FR4 Frankfurt-Griesheim Data Center   
...                                    ...   
169                  Frankfurt Data Center   
170              DE1 Frankfurt Data Center   
171                 Leverkusen Data Center   
172                   Chemnitz Data Center   
173                      LIM 1 Data Center   

                                                 Address  \
Index                                                      
0      Eschborner Landstraße 100, 60489 Frankfurt am ...   
1                             Frankfurt am Main, Germany   
2                Kruppstraße 121-127, Frankfurt, Germany   
3                    Kleyerstraße 90, Frankfurt, Germany   
4                  Lärchenstraße 110, Frankfurt, Germany   
...                                                  ...   
169                Gutleutstraße 310, Frankfurt, Germany   
170    Equinix FR6, Frankfurt, Frankfurt am Main West...   
171    Dornierstraße 10, 51381 Leverkusen-Quettingen,...   
172    Rochlitzer Straße 19, 09111 Chemnitz, Chemnitz...   
173    Rheingönheimer Weg 13, 67117 Limburgerhof, Ger...   

                                                  Href  \
Index                                                    
0                                    /amazon-aws-fra54   
1      /microsoft-azure-germany-west-central-frankfurt   
2                            /hetzner-park-falkenstein   
3               /oracle-germany-central-eu-frankfurt-1   
4                                    /amazon-aws-fra52   
...                                                ...   
169                                 /centerserv-bremen   
170                           /zenlayer-fra3-frankfurt   
171                                /atos-group-germany   
172                       /lumen-berlin-kitzingstrasse   
173                         /lumen-berlin-gradestrasse   

                                             Description     Phone Number  \
Index                                                                       
0      Amazon AWS FRA54 is located at Eschborner Land...  +1 844-902-4700   
1      Microsoft Azure Germany West Central-Frankfurt...  +1 833-538-1100   
2      Hetzner Data Center Park Falkenstein is locate...  +1 877-857-4410   
3      Oracle Germany Central eu-frankfurt-1 is locat...  +1 833-456-7700   
4      Amazon AWS FRA52 is located at Weismüllerstraß...  +1 844-902-4700   
...                                                  ...              ...   
169    CenterServ Bremen Data Center is located at Br...  +1 833-544-2200   
170    Zenlayer FRA3 Frankfurt Data Center is located...  +1 866-417-8330   
171    Atos Group Germany Data Center is located at W...  +1 833-456-7700   
172    Lumen Berlin Kitzingstraße Data Center is loca...  +1 877-881-6530   
173    Lumen Berlin Gradestraße Data Center is locate...  +1 877-881-6530   

      Bare Metal      IaaS Internet Exchange Colocation_x  \
Index                                                       
0       Inactive  Inactive          Inactive       Active   
1       Inactive  Inactive            Active       Active   
2         Active  Inactive            Active       Active   
3         Active  Inactive          Inactive     Inactive   
4       Inactive  Inactive          Inactive       Active   
...          ...       ...               ...          ...   
169     Inactive  Inactive          Inactive       Active   
170     Inactive  Inactive          Inactive       Active   
171     Inactive  Inactive          Inactive     Inactive   
172     Inactive  Inactive            Active       Active   
173     Inactive  Inactive            Active       Active   

                    Products                         Airplane  \
Index                                     

In [ ]:
country_df = pd.concat([Canada_df, UK_df])
country_df = pd.concat([country_df, Germany_df])
country_df.reset_index(drop=True)

Name  \
0                 Canada Central-Toronto   
1               TR2 Toronto Data Centers   
2           MT1 Montreal IBX Data Center   
3            CL3 Calgary IBX Data Center   
4    YYZ1 Mississauga Data Center Campus   
..                                   ...   
497                Frankfurt Data Center   
498            DE1 Frankfurt Data Center   
499               Leverkusen Data Center   
500                 Chemnitz Data Center   
501                    LIM 1 Data Center   

                                               Address  \
0                                  Toronto, ON, Canada   
1            45 Parliament Street, Toronto, ON, Canada   
2    6205 Rue Vanden Abeele, Saint-Laurent, QC, Canada   
3          5300 86 Ave SE, Calgary, AB T2C 2R6, Canada   
4        6800 Millcreek Drive, Mississauga, ON, Canada   
..                                                 ...   
497              Gutleutstraße 310, Frankfurt, Germany   
498  Equinix FR6, Frankfurt, Frankfurt am Main West...   
499  Dornierstraße 10, 51381 Leverkusen-Quettingen,...   
500  Rochlitzer Straße 19, 09111 Chemnitz, Chemnitz...   
501  Rheingönheimer Weg 13, 67117 Limburgerhof, Ger...   

                                        Href  \
0    /microsoft-azure-canada-central-toronto   
1                    /vantage-qc1-montreal-i   
2                                  /ovh-bhs2   
3     /core-data-centres-markham-data-centre   
4         /cogent-communications-mississauga   
..                                       ...   
497                       /centerserv-bremen   
498                 /zenlayer-fra3-frankfurt   
499                      /atos-group-germany   
500             /lumen-berlin-kitzingstrasse   
501               /lumen-berlin-gradestrasse   

                                           Description     Phone Number  \
0    Microsoft Azure Canada Central-Toronto is loca...  +1 833-538-1100   
1    Vantage Data Centers QC1 Montreal I Data Cente...  +1 866-445-9110   
2    OVHCloud BHS2 Data Center is located at 50 Rue...  +1 833-476-4400   
3    CORE Data Centres Markham Data Centre is locat...  +1 877-881-6530   
4    Cogent Communications Mississauga Data Center ...  +1 844-823-6300   
..                                                 ...              ...   
497  CenterServ Bremen Data Center is located at Br...  +1 833-544-2200   
498  Zenlayer FRA3 Frankfurt Data Center is located...  +1 866-417-8330   
499  Atos Group Germany Data Center is located at W...  +1 833-456-7700   
500  Lumen Berlin Kitzingstraße Data Center is loca...  +1 877-881-6530   
501  Lumen Berlin Gradestraße Data Center is locate...  +1 877-881-6530   

    Bare Metal      IaaS Internet Exchange Colocation_x  \
0     Inactive  Inactive            Active       Active   
1     Inactive  Inactive            Active       Active   
2     Inactive  Inactive            Active       Active   
3       Active  Inactive            Active       Active   
4     Inactive  Inactive            Active       Active   
..         ...       ...               ...          ...   
497   Inactive  Inactive          Inactive       Active   
498   Inactive  Inactive          Inactive       Active   
499   Inactive  Inactive          Inactive     Inactive   
500   Inactive  Inactive            Active       Active   
501   Inactive  Inactive            Active       Active   

                  Products                         Airplane  \
0    0 colocation products  224.32 miles to nearest airport   
1    0 colocation products  254.77 miles to nearest airport   
2    0 colocation products  248.55 miles to nearest airport   
3    0 colocation products   232.4 miles to nearest airport   
4    0 colocation products   65.87 miles to nearest airport   
..                     ...                              ...   
497  0 colocation products                              NaN   
498  0 colocation products    9.33 miles to nearest airport   
499  0 colocation products    5.09 miles to nearest airp

In [ ]:
country_df.to_csv('Three Countries.csv', index=False)